## Get the dataset

I will use crangfield dataset for apply some aproachs


In [1]:
import numpy as np
import json
import os
import gc
from collections import defaultdict
from gensim.models.keyedvectors import KeyedVectors
from gensim.models import TfidfModel
from gensim import corpora,similarities,matutils
from gensim.parsing.preprocessing import remove_stopwords
from nltk.tokenize import word_tokenize


docs = [(doc["id"],(doc["title"]+doc["body"])) for doc in json.load(open("crag_doc.json","r"))]
queries = [(query["query number"],query["query"]) for query in json.load(open("crag_queries.json","r"))][:-1]
relevance = json.load(open("crag_relevance.json","r"))

#try use dictionaries

docs = { k:v for k,v in docs}
queries = { k:v for k,v in queries}

#remove stop words
#docs = { k:remove_stopwords(v) for k,v in docs}
#queries = { k:remove_stopwords(v) for k,v in queries}

print("Num documents",len(docs),"Num queries",len(queries))




c:\users\asus\anaconda3\envs\bio\lib\site-packages\gensim\utils.py:1212: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


Num documents 1400 Num queries 225


In [2]:
#create a queries relevance list
query_relevance = defaultdict(list)

[query_relevance[line["query_num"]].append((line["id"],line["position"])) for line in relevance]

query_relevance = [(k,list(map(lambda t:t[0],sorted(v, key=lambda x:-x[1])))) for k,v in query_relevance.items()]
query_relevance = { k:v for k,v in query_relevance}

In [3]:

#list of words in the data
dataset_words = set()

for q in queries.values():
    dataset_words |= set(word_tokenize(q))
    
for doc in docs.values():
    dataset_words |= set(word_tokenize(doc))
    
dataset_len_vocabulary = len(dataset_words)


## Load the embeddings

Google news negative 300 dim

In [9]:
PATH = os.path.join("..","data","GoogleNews-vectors-negative300.bin")

PATH_CRAG = "CRAG_IN_FROM_BIG_FILE_NLTK_TOKENIZER.bin"

model = KeyedVectors.load_word2vec_format(PATH_CRAG, binary=True)

print("Model shape",model.vectors.shape)

Model shape (6796, 200)


In [11]:
len(model.index2word)

6796

In [12]:
print("Percentage of words coverd by the pre trained embedding",(len(set(model.index2word)&dataset_words)/dataset_len_vocabulary) )

#CREATE A SMALLER EMBEDDING ONLY CONTAIN THE NEEDED WORDS

words_used = []
words_emb_list = []
for word in dataset_words:
    try:
        words_emb_list.append( model.get_vector(word))
        words_used.append(word)
    except KeyError:
        pass #word2vec model doenst have that word
    
words_emb_matrix = np.vstack(words_emb_list)
    
small_model = KeyedVectors(words_emb_matrix.shape[1])
small_model.add(entities=words_used,weights=words_emb_matrix)
small_model.init_sims(True)

#RELEASE THE BIG WORD2VEC EMBEDDING
del model
del words_emb_matrix
gc.collect()


Percentage of words coverd by the pre trained embedding 0.6652310101801097


0

## Get embbedings of the words of documents

Creating some auxiliar functions

In [16]:
def doc2wordListVec(corpus_dict,get_embedding=lambda x:small_model.get_vector(x) ):
    
    docs_emb = []

    for i,e in corpus_dict.items():

        doc_emb = []

        for token in word_tokenize(e):
            try:
                doc_emb.append( get_embedding(token))
            except KeyError:
                pass #word2vec model doenst have that word

        if len(doc_emb)==0:
            print("miss id ",i)
            continue

        docs_emb.append((i,doc_emb))
        
    return docs_emb

def get_doc_id(docs_emb,results):
    return [ (docs_emb[k][0],v) for k,v in results]
        
def _sim_cos_vec(embedding_matrix,norm_matrix,word_vec):
    
    dot_product = np.dot(embedding_matrix ,word_vec)

    norm_word = np.linalg.norm(word_vec)

    norm = norm_matrix * norm_word

    return dot_product/ norm


def get_top_k_similars(similaraty_function, docs_concat_emb , queries_avg_emb, query_relevance, top_k=50):
    
    list_recall = []
    list_precision = []
    for query_id,query_vec in queries_avg_emb:

        sims = sorted(enumerate(similaraty_function(query_vec)), key=lambda item: -item[1])

        docs_top_k_id = [str(k) for k,v in get_doc_id(docs_concat_emb,sims[:top_k])]
        docs_relevant = set(query_relevance[str(query_id)])
        
        #not needed for recall
        order_intersect = [ doc for doc in docs_top_k_id if doc in docs_relevant]
        
        list_recall.append(len(order_intersect)/len(query_relevance[str(query_id)]))
        list_precision.append(len(order_intersect)/top_k)
        
    return list_recall,list_precision

## Define some varibles

In [17]:
TOP_K = 50

## First approach 

convert document to average of their embeddings

In [18]:

docs_emb = doc2wordListVec(docs)

docs_avg_emb = [ (i,sum(doc_emb)/len(doc_emb))  for i,doc_emb in docs_emb ]
doc_emb_matrix = np.vstack([v for k, v in docs_avg_emb])

doc_emb_norm_matrix = np.linalg.norm(doc_emb_matrix, axis=1) #pre compute l2-norm



miss id  471
miss id  995


In [19]:
docs_emb_avg_indexer = similarities.MatrixSimilarity(matutils.Dense2Corpus(doc_emb_matrix.T))

c:\users\asus\anaconda3\envs\bio\lib\site-packages\gensim\matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int32 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):


In [20]:
queries_emb = doc2wordListVec(queries)

queries_avg_emb = [ (i,sum(q)/len(q))  for i,q in queries_emb ]

In [21]:


#Calculate the average recall for the dataset
recall,precision = get_top_k_similars(lambda q:docs_emb_avg_indexer[q],docs_avg_emb,queries_avg_emb,query_relevance,top_k=TOP_K)

print("Using gensim cos sim, RECALL",sum(recall)/len(recall),"PRECISION",sum(precision)/len(precision))

#Calculate the average recall for the dataset but using my implementation of the cos similaraty
recall,precision = get_top_k_similars(lambda q:_sim_cos_vec(doc_emb_matrix,doc_emb_norm_matrix,q),docs_avg_emb,queries_avg_emb,query_relevance,top_k=TOP_K)

print("Using my implementation of cos sim, RECALL",sum(recall)/len(recall),"PRECISION",sum(precision)/len(precision))


Using gensim cos sim, RECALL 0.29761692145967084 PRECISION 0.0425777777777777
Using my implementation of cos sim, RECALL 0.29761692145967084 PRECISION 0.0425777777777777


## Second approach

Convert document to average and add tf-idf as weigh

Formula to calculate the token (t) embbeding 

\begin{equation}
\overrightarrow{t} = \frac{\sum_{j=1}^{|V|} \overrightarrow{w_{j}} \cdot TF(w_{j},t) \cdot IDF(w_{j})}{\sum_{j=1}^{|V|} TF(w_{j},t) \cdot IDF(w_{j})}
\end{equation}

What i think this formula will do:

 - Will reorganize the multidimentional space based on the most "relevant" words in terms of tf idf
 - Documents with most "relevant" words will became closer, because of the process of weight average with tf-idf

In [24]:
docs_tokens = [ word_tokenize(doc) for doc in docs.values() ]

corpora_docs = corpora.Dictionary(docs_tokens)
corpora_docs_bow = [corpora_docs.doc2bow(line) for line in docs_tokens]  # convert corpus to BoW format
tfidf = TfidfModel(corpora_docs_bow)  # fit model

def doc2AVGwordListVec_TFIDF(corpus_dict,corpora_docs,tfidf,get_embedding=lambda x:small_model.get_vector(x)):
    
    #create tf idf model for the dataset
    docs_tokens = [ word_tokenize(doc) for doc in corpus_dict.values() ]
    
    docs_emb = []

    for i,e in corpus_dict.items():

        doc_emb = {}
        doc_tokens_used = []
        for token in word_tokenize(e):
            try:
                doc_emb[token] = get_embedding(token) 
                doc_tokens_used.append(token)
            except KeyError:
                pass #word2vec model doenst have that word

        if len(doc_emb)==0:
            print("miss id ",i)
            continue

        doc_bow = corpora_docs.doc2bow(doc_tokens_used)
        sentence_tfidf = tfidf[doc_bow]
        sum_tfidf = 0

        for token_id,_tfidf in sentence_tfidf:
            token = corpora_docs[token_id]
            doc_emb[token] = doc_emb[token]*_tfidf
            sum_tfidf += _tfidf

        docs_emb.append((i,sum(doc_emb.values())/sum_tfidf))
        
    return docs_emb

In [25]:
docs_avg_emb_tfidf = doc2AVGwordListVec_TFIDF(docs,corpora_docs,tfidf)
docs_emb_matrix_tfidf = np.vstack([v for k, v in docs_avg_emb_tfidf])
docs_emb_avg_tfidf_indexer = similarities.MatrixSimilarity(matutils.Dense2Corpus(docs_emb_matrix_tfidf.T))

queries_emb_tfidf = doc2AVGwordListVec_TFIDF(queries,corpora_docs,tfidf)

recall,precision = get_top_k_similars(lambda q:docs_emb_avg_tfidf_indexer[q],docs_avg_emb_tfidf,queries_emb_tfidf,query_relevance,top_k=TOP_K)

print("RECALL",sum(recall)/len(recall),"PRECISION",sum(precision)/len(precision))



miss id  471
miss id  995
RECALL 0.31666370953657164 PRECISION 0.044266666666666565


In [31]:

"""

DEBUG CELL TF IDF


docs_tokens = [ tokenize(doc) for doc in docs.values() ]

corpora_docs = corpora.Dictionary(docs_tokens)
corpora_docs_bow = [corpora_docs.doc2bow(line) for line in docs_tokens]  # convert corpus to BoW format
tfidf = TfidfModel(corpora_docs_bow)  # fit model

docs_emb = []

for i,e in list(docs.items()):

    doc_emb = {}
    doc_tokens_used = []
    for token in tokenize(e):
        try:
            doc_emb[token] = small_model.get_vector(token) 
            doc_tokens_used.append(token)
        except KeyError:
            pass #word2vec model doenst have that word

    if len(doc_emb)==0:
        print("miss id ",i)
        continue
    
    doc_bow = corpora_docs.doc2bow(doc_tokens_used)
    sentence_tfidf = tfidf[doc_bow]
    sum_tfidf = 0
    
    for token_id,_tfidf in sentence_tfidf:
        token = corpora_docs[token_id]
        doc_emb[token] = doc_emb[token]*_tfidf
        sum_tfidf += _tfidf
    
    docs_emb.append((i,sum(doc_emb.values())/sum_tfidf ))
"""    


    


'\n\nDEBUG CELL TF IDF\n\n\ndocs_tokens = [ tokenize(doc) for doc in docs.values() ]\n\ncorpora_docs = corpora.Dictionary(docs_tokens)\ncorpora_docs_bow = [corpora_docs.doc2bow(line) for line in docs_tokens]  # convert corpus to BoW format\ntfidf = TfidfModel(corpora_docs_bow)  # fit model\n\ndocs_emb = []\n\nfor i,e in list(docs.items()):\n\n    doc_emb = {}\n    doc_tokens_used = []\n    for token in tokenize(e):\n        try:\n            doc_emb[token] = small_model.get_vector(token) \n            doc_tokens_used.append(token)\n        except KeyError:\n            pass #word2vec model doenst have that word\n\n    if len(doc_emb)==0:\n        print("miss id ",i)\n        continue\n    \n    doc_bow = corpora_docs.doc2bow(doc_tokens_used)\n    sentence_tfidf = tfidf[doc_bow]\n    sum_tfidf = 0\n    \n    for token_id,_tfidf in sentence_tfidf:\n        token = corpora_docs[token_id]\n        doc_emb[token] = doc_emb[token]*_tfidf\n        sum_tfidf += _tfidf\n    \n    docs_emb.appen

## Third approach CHANGE!!!! ERROR IN THE IMPLEMENTATION

Query embedding by averaging each word embedding is wrong. Instead compute cos sim of each word with DOC AVG EMBEDDING and then do the average!

Using IN and OUT matrix

In [26]:
PATH_CRAG = "CRAG_OUT_FROM_BIG_FILE.bin"

model_out = KeyedVectors.load_word2vec_format(PATH_CRAG, binary=True)
model_out.init_sims(True)
print(model_out.vectors.shape)

(7143, 200)


In [27]:
docs_emb = doc2wordListVec(docs, get_embedding = lambda x:model_out.get_vector(x))

docs_avg_emb = [ (i,sum(doc_emb)/len(doc_emb))  for i,doc_emb in docs_emb ]
docs_emb_matrix = np.vstack([v for k, v in docs_avg_emb])
docs_emb_norm_matrix = np.linalg.norm(docs_emb_matrix, axis=1) #pre compute l2-norm

queries_emb = doc2wordListVec(queries)

queries_avg_emb = [ (i,sum(query_emb)/len(query_emb))  for i,query_emb in queries_emb ]

print(queries_avg_emb[0][1].shape)

recall,precision = get_top_k_similars(lambda q:_sim_cos_vec(docs_emb_matrix,docs_emb_norm_matrix,q),docs_avg_emb,queries_avg_emb,query_relevance,top_k=TOP_K)

print("Using gensim cos sim, RECALL",sum(recall)/len(recall),"PRECISION",sum(precision)/len(precision))


miss id  471
miss id  995
(200,)
Using gensim cos sim, RECALL 0.17994551157496608 PRECISION 0.02675555555555553


In [31]:
model_out.similar_by_word("airplane")

[('airplanes', 0.874048113822937),
 ('plane', 0.8673020601272583),
 ('aircraft', 0.8120570778846741),
 ('planes', 0.8073369860649109),
 ('airliner', 0.786501407623291),
 ('helicopter', 0.7701968550682068),
 ('fuselages', 0.7683353424072266),
 ('taxiing', 0.7674869298934937),
 ('aeroplane', 0.7613992691040039),
 ('flight', 0.7520362734794617)]

In [30]:
small_model.similar_by_word("airplane")

[('plane', 0.8403297547717599),
 ('airplanes', 0.8247849536192389),
 ('planes', 0.7030570748158856),
 ('aircraft', 0.6820166998839781),
 ('helicopter', 0.6575045486040091),
 ('airliner', 0.6474933314495913),
 ('flying', 0.603546082242043),
 ('aeroplane', 0.5902226207868351),
 ('fuselage', 0.5674461992715145),
 ('ailerons', 0.5581440682371379)]

In [32]:
docs_emb = doc2wordListVec(docs)

docs_avg_emb = [ (i,sum(doc_emb)/len(doc_emb))  for i,doc_emb in docs_emb ]
docs_emb_matrix = np.vstack([v for k, v in docs_avg_emb])
docs_emb_norm_matrix = np.linalg.norm(doc_emb_matrix, axis=1) #pre compute l2-norm

queries_emb = doc2wordListVec(queries)

r = []
query_id,emb = queries_emb[0]
for q in emb:
    r.append(_sim_cos_vec(docs_emb_matrix,docs_emb_norm_matrix,q))

r = sum(r)/len(r)

sims = sorted(enumerate(r), key=lambda item: -item[1])

docs_top_k_id = [str(k) for k,v in get_doc_id(docs_avg_emb,sims[:50])]

docs_relevant = set(query_relevance[str(query_id)])
        
#not needed for recall
order_intersect = [ doc for doc in docs_top_k_id if doc in docs_relevant]
print(len(order_intersect))
print(len(order_intersect)/len(query_relevance[str(query_id)]))
print(len(order_intersect)/50)



miss id  471
miss id  995
6
0.20689655172413793
0.12


In [106]:
queries_emb

[(1, [array([-1.01211965, -2.01888561,  1.95050526, -1.09446144, -0.94116879,
           4.60933542,  2.43990469, -0.93573236, -4.08491707,  1.55335009,
           1.93396962,  0.09101694,  0.61537188, -3.15975237,  2.04422712,
           0.75288296, -0.62381184,  2.10537291, -0.38636041,  1.63608015,
           0.20662107,  0.32282153, -2.9686203 ,  1.06517506, -1.54379249,
          -0.81059235,  1.1056776 , -2.95529771, -2.33027339, -2.94670129,
           4.1049614 , -0.81510657, -1.03413963, -3.21383142,  0.16296193,
           2.05648303,  1.02135837,  1.71398151, -0.38968307,  0.24374127,
          -4.96552515,  0.82721591, -1.76985955,  3.37734437, -4.82410383,
          -2.2758646 , -0.20623781,  1.62682533, -0.86621356,  3.36710668,
           0.9143911 ,  0.43254378, -1.82421756,  3.09909964,  0.5991174 ,
          -0.58188266, -4.02629566, -2.33697796,  0.82258779, -0.99076283,
           1.07958984,  3.23040509,  0.32820117,  4.62943172, -0.27817327,
           1.644485  ,